In [1]:
import pandas as pd
import numpy as np 
import glob
import os 
from openpyxl import load_workbook
from openpyxl.styles import PatternFill, Font
from datetime import datetime

In [2]:
hoje = datetime.today().strftime('%Y-%m-%d')

In [3]:
#precisa ver duplicidade de desc e vendas irece.

In [4]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C15\TABELA DE PEDIDOS\Pedidos Semanais Especiais - BOT - 202515 (1).xlsx")

df_tabela = df_tabela[df_tabela['Ação revendedor'].notna() | df_tabela['Ação consumidor'].notna()]

df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 

df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm')]

#df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")

df_tabela = df_tabela[(df_tabela['Categoria'] != "EMBALAGENS") | (df_tabela['Categoria'] != "SUPORTE À VENDA")]

#df_tabela = df_tabela[df_tabela['Tipo de pedido'] == 'Semanal']

df_tabela = df_tabela[~df_tabela['Descrição'].str.contains('PRM')]

df_tabela = df_tabela[df_tabela['Tipo de produto']!= 'EDICAO LIMITADA']

df_tabela['Ação revendedor'] = np.where(df_tabela['Ação revendedor'].isna(),df_tabela['Ação consumidor'],df_tabela['Ação revendedor'])

df_tabela['Percentual de desconto revendedor'] = np.where(df_tabela['Percentual de desconto revendedor'].isna(),df_tabela['Percentual de desconto consumidor'],df_tabela['Percentual de desconto revendedor'])

df_tabela['MATCH'] = 1



In [5]:
import pyodbc
import configparser

#query de vendas por ciclo

config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\Documents\Enviador de email\credenciais.ini")

conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

query = f'''
SELECT 
    B.PDV, 
    B.SKU,
    bd.SKU2, 
    COALESCE(bd.SKU2, b.SKU) AS SKU_FINAL,
    B.DESCRICAO,
    SUM(CAST(b.VENDAS AS DECIMAL(18,2))) AS VENDAS_CICLO,
    C.Ciclo
FROM base_vendas_bi b
INNER JOIN ciclos_data_2025 c 
    ON CAST(b.[DATA] AS DATE) = CONVERT(DATE, c.[Date], 103) AND C.MARCA = 'BOT'
LEFT JOIN base_depara bd on b.SKU = bd.SKU 
WHERE CAST(b.[DATA] AS DATE) >= DATEADD(YEAR, -1, GETDATE())
GROUP BY
    B.PDV, 
    B.SKU,
    bd.SKU2,
    B.DESCRICAO,
    C.Ciclo
HAVING SUM(CAST(b.VENDAS AS DECIMAL(18,2))) > 0
'''
dfi = pd.read_sql(query, conn)
conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_2580\2225685327.py:39: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dfi = pd.read_sql(query, conn)


In [6]:
dfi['SKU2'] = dfi['SKU2'].fillna("-")

In [7]:
dfi = dfi[dfi['SKU2'] == "-"]

dfi.head()

PDV    SKU SKU2  SKU_FINAL                                DESCRICAO  \
0  20998  79437    -      79437   QDB GLIT SLT P/OLHO ROSELITTER 1g RPCK   
1   4560  51226    -      51226            CBEM SAB BARRA NUVEM V5 2x80g   
2  21277  48290    -      48290     NSPA DES COL BDY SPLSH AMEI 200ml V2   
3  23701  56810    -      56810  MATCH COND SCIENCE CRESCIMENTO V2 280ml   
4   5699  56027    -      56027                      MEN SAB BARRA 2x90g   

   VENDAS_CICLO    Ciclo  
0           1.0  C202413  
1          30.0  C202413  
2           3.0  C202414  
3           2.0  C202505  
4          37.0  C202506

In [8]:

# 1. Agrupamento
df_agrupado = dfi.groupby(['PDV', 'SKU_FINAL', 'DESCRICAO', 'Ciclo'], as_index=False)['VENDAS_CICLO'].sum()

# 2. Pivotar o DataFrame
df_pivotado = df_agrupado.pivot_table(
    index=['PDV', 'SKU_FINAL', 'DESCRICAO'],
    columns='Ciclo',
    values='VENDAS_CICLO',
    fill_value=0  # Substitui NaN por 0
)

# 3. Resetar o índice para deixar como DataFrame normal (opcional)
df_pivotadowawa = df_pivotado.reset_index()

# 4. (Opcional) Renomear colunas com prefixo "Ciclo_"
df_pivotadowawa.columns.name = None
df_pivotadowawa = df_pivotadowawa.rename(columns=lambda x: f'Ciclo_{x}' if isinstance(x, (int, str)) and str(x).isdigit() else x)

# Resultado final
df_pivotadowawa.head()


PDV  SKU_FINAL                             DESCRICAO  C202412  C202413  \
0  12522       1004         FLORATTA DES COL MY BLUE 75ml      0.0     15.0   
1  12522       1080  INTENSE GLOS LAB BUBBAL TUT/FRUT 5ml      0.0      0.0   
2  12522       1296   PMPCK THE BLEND DES ANTIT AER 2x75g      0.0      1.0   
3  12522       1302        PMPCK LILY DES ANTIT AER 2x75g      1.0      4.0   
4  12522       1314        PMPCK ZAAD DES ANTIT AER 2x75g      0.0      2.0   

   C202414  C202415  C202416  C202417  C202501  ...  C202503  C202504  \
0      2.0      3.0     56.0      6.0      1.0  ...      1.0      5.0   
1      4.0      0.0     10.0      2.0      2.0  ...      2.0      3.0   
2      3.0      3.0      2.0      0.0      0.0  ...      0.0      0.0   
3      3.0      5.0      6.0      0.0      0.0  ...      0.0      0.0   
4      3.0      1.0      1.0      0.0      0.0  ...      0.0      0.0   

   C202505  C202506  C202507  C202508  C202509  C202510  C202511  C202512  
0     12.0      7.0      2.0      0.0      1.0      2.0      5.0      2.0  
1      1.0      7.0     17.0      0.0      0.0      0.0      0.0      0.0  
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
3      0.0      3.0      4.0      0.0      4.0      4.0      2.0      1.0  
4      0.0      0.0      0.0      0.0      0.0      0.0      1.0      1.0  

[5 rows x 21 columns]

In [9]:
df_pivotadowawa[(df_pivotadowawa['SKU_FINAL'] == '1634') & (df_pivotadowawa['PDV'] == '20998')]

Empty DataFrame
Columns: [PDV, SKU_FINAL, DESCRICAO, C202412, C202413, C202414, C202415, C202416, C202417, C202501, C202502, C202503, C202504, C202505, C202506, C202507, C202508, C202509, C202510, C202511, C202512]
Index: []

[0 rows x 21 columns]

In [10]:


df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv_origi = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv[df_pdv['GESTÃO']!="Inativa"]

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO', 'STATUS'])

df_pdv = df_pdv[df_pdv['CANAL']!='MTZ']

#df_pdv['CANAL'] = np.where((df_pdv['CANAL']=='LJ')|(df_pdv['CANAL']=='HIB')|(df_pdv['CANAL']=='CD'),'TODOS','VD')

df_pdv['MATCH'] = 1

df_pdv = df_pdv[(df_pdv['PDV']!=910291)&(df_pdv['PDV']!=910173)]



In [11]:
df_pdv[df_pdv['PDV']==21007]

PDV CANAL DESCRIÇÃO PDV         PDV DESC  UF        MARCA ANALISTA  \
43  21007    LJ     MOREIRA 2  21007-MOREIRA 2  AL  O BOTICARIO     LUAN   

        SUPERVISOR  MATCH  
43  Maxwell Vieira      1

In [12]:
df_pdv = df_pdv.drop(columns=['PDV DESC'])

In [13]:
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

query_est_draft = f'''
select em.PDV ,
COALESCE(em.SKU_PARA , em.SKU) as SKU,
em.DESCRICAO,
d.salescurve as curva,
d.codcategory as categoria,
d.nextcycleprojection as proj_mar
,d.secondtonextcycleprojection as 'proj_mar+1',
em.[ESTOQUE ATUAL],em.[ESTOQUE EM TRANSITO],
em.[PEDIDO PENDENTE],
em.[DDV PREVISTO] ,
d.pricesellin as 'preço'
from estoque_mar em 
left join draft d on d.code = COALESCE(em.SKU_PARA , em.SKU) and d.loja_id = em.PDV 
where em.ORIGEM = 'BOT'
'''
df_draft_ = pd.read_sql(query_est_draft, conn)
conn.close()

#FALTA ATUALIZAR QUERY

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_2580\268247862.py:25: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_draft_ = pd.read_sql(query_est_draft, conn)


In [14]:
df_draft = df_draft_

In [15]:
df_draft[df_draft['SKU']=='1634']

PDV   SKU                           DESCRICAO curva categoria  \
128590  24293  1634  NSPA GEL ESF CPO MORANGO RUBY 175G  None      None   
128840  21278  1634  NSPA GEL ESF CPO MORANGO RUBY 175G  None      None   
128956  12826  1634  NSPA GEL ESF CPO MORANGO RUBY 175G  None      None   
129361   4560  1634  NSPA GEL ESF CPO MORANGO RUBY 175G  None      None   
129451   5699  1634  NSPA GEL ESF CPO MORANGO RUBY 175G  None      None   
...       ...   ...                                 ...   ...       ...   
337558  21647  1634  NSPA GEL ESF CPO MORANGO RUBY 175G  None      None   
345348  20009  1634  NSPA GEL ESF CPO MORANGO RUBY 175G  None      None   
349112  20968  1634  NSPA GEL ESF CPO MORANGO RUBY 175G  None      None   
358656  12830  1634  NSPA GEL ESF CPO MORANGO RUBY 175G  None      None   
359288  20997  1634  NSPA GEL ESF CPO MORANGO RUBY 175G  None      None   

        proj_mar  proj_mar+1 ESTOQUE ATUAL ESTOQUE EM TRANSITO  \
128590       NaN         NaN             3                   0   
128840       NaN         NaN             2                   0   
128956       NaN         NaN             3                   0   
129361       NaN         NaN             5                   0   
129451       NaN         NaN             4                   0   
...          ...         ...           ...                 ...   
337558       NaN         NaN             4                   0   
345348       NaN         NaN            10                   0   
349112       NaN         NaN             8                   0   
358656       NaN         NaN             5                   0   
359288       NaN         NaN             3                   0   

       PEDIDO PENDENTE DDV PREVISTO  preço  
128590               0            0    NaN  
128840               0            0    NaN  
128956               0            0    NaN  
129361               0            0    NaN  
129451               0         0,05    NaN  
...                ...          ...    ...  
337558               0            0    NaN  
345348               0            0    NaN  
349112               0            0    NaN  
358656               0            0    NaN  
359288               0            0    NaN  

[73 rows x 12 columns]

In [16]:
df_draft = df_draft[~df_draft['DESCRICAO'].str.contains('OUI', na=False)]

df_draft.shape

(350945, 12)

In [17]:
df_draft['ESTOQUE ATUAL'] = df_draft['ESTOQUE ATUAL'].astype(float)

df_draft['ESTOQUE EM TRANSITO'] = df_draft['ESTOQUE EM TRANSITO'].astype(float)

df_draft['PEDIDO PENDENTE'] = df_draft['PEDIDO PENDENTE'].astype(float)

df_draft.dtypes

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_2580\1765304903.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['ESTOQUE ATUAL'] = df_draft['ESTOQUE ATUAL'].astype(float)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_2580\1765304903.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['ESTOQUE EM TRANSITO'] = df_draft['ESTOQUE EM TRANSITO'].astype(float)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_2580\1765304903.py:5: SettingWithCopyWarning: 
A value is trying to b

PDV                     object
SKU                     object
DESCRICAO               object
curva                   object
categoria               object
proj_mar               float64
proj_mar+1             float64
ESTOQUE ATUAL          float64
ESTOQUE EM TRANSITO    float64
PEDIDO PENDENTE        float64
DDV PREVISTO            object
preço                  float64
dtype: object

In [18]:
df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].str.replace(',','.')

df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].astype(float)

df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].fillna(0)

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_2580\1952797845.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].str.replace(',','.')
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_2580\1952797845.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].astype(float)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_2580\1952797845.py:5: SettingWithCopyWarning: 
A value is trying to be set on 

In [19]:
df_draft = df_draft.groupby(['PDV','SKU','curva','categoria'])[['proj_mar','proj_mar+1','ESTOQUE ATUAL','ESTOQUE EM TRANSITO','PEDIDO PENDENTE','DDV PREVISTO','preço']].max().reset_index()

In [20]:
df_tabela = df_tabela.drop_duplicates()

In [21]:
df_bi_preco = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C13\preço BI\TABELA DE PREÇOS (2).xlsx")

df_bi_preco = df_bi_preco.drop(columns=['Tipo Preço','CATEGORIA','LINHA','MARCA'])



In [22]:
df_pivotadowawa['SKU_FINAL'] = df_pivotadowawa['SKU_FINAL'].astype('str')

In [23]:
df_pivotadowawa['SKU_FINAL'] = df_pivotadowawa['SKU_FINAL'].astype(str)

df_pivotadowawa['SKU_FINAL'].head()

0    1004
1    1080
2    1296
3    1302
4    1314
Name: SKU_FINAL, dtype: object

In [24]:
df_draft[df_draft['SKU']=='1634']

Empty DataFrame
Columns: [PDV, SKU, curva, categoria, proj_mar, proj_mar+1, ESTOQUE ATUAL, ESTOQUE EM TRANSITO, PEDIDO PENDENTE, DDV PREVISTO, preço]
Index: []

In [25]:
df_draft = pd.merge(df_draft,df_pivotadowawa,left_on=['PDV','SKU'],right_on=['PDV','SKU_FINAL'],how='inner')

In [26]:
df_draft[df_draft['SKU']=='1634']

Empty DataFrame
Columns: [PDV, SKU, curva, categoria, proj_mar, proj_mar+1, ESTOQUE ATUAL, ESTOQUE EM TRANSITO, PEDIDO PENDENTE, DDV PREVISTO, preço, SKU_FINAL, DESCRICAO, C202412, C202413, C202414, C202415, C202416, C202417, C202501, C202502, C202503, C202504, C202505, C202506, C202507, C202508, C202509, C202510, C202511, C202512]
Index: []

[0 rows x 31 columns]

In [27]:
df_final = pd.merge(left=df_tabela,right=df_pdv,on='MATCH',how='left')

df_final = df_final.drop_duplicates()

df_final.shape

(34265, 31)

In [28]:
df_final['PDV'].value_counts()

PDV
12522    445
12817    445
12818    445
12820    445
12823    445
        ... 
24257    445
24268    445
24269    445
24293    445
23813    445
Name: count, Length: 77, dtype: int64

In [29]:
df_draft[(df_draft['SKU'] == '52627') & (df_draft['PDV'] == '3546') ].head()

PDV    SKU curva         categoria  proj_mar  proj_mar+1  \
74681  3546  52627     B  CUIDADOS FACIAIS       2.0         2.0   
74682  3546  52627     B  CUIDADOS FACIAIS       2.0         2.0   

       ESTOQUE ATUAL  ESTOQUE EM TRANSITO  PEDIDO PENDENTE  DDV PREVISTO  ...  \
74681            0.0                  2.0              0.0          0.09  ...   
74682            0.0                  2.0              0.0          0.09  ...   

       C202503 C202504 C202505  C202506  C202507  C202508  C202509  C202510  \
74681      5.0     0.0     0.0      0.0      0.0      0.0      0.0      0.0   
74682      0.0     0.0     4.0      3.0      0.0      3.0      4.0      1.0   

       C202511  C202512  
74681      0.0      0.0  
74682      3.0      3.0  

[2 rows x 31 columns]

In [30]:
df_draft = df_draft.drop(columns='DESCRICAO')

df_draft.columns

Index(['PDV', 'SKU', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', 'C202412', 'C202413', 'C202414',
       'C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511', 'C202512'],
      dtype='object')

In [31]:
numericos = df_draft.columns[-18:]

chaves = [col for col in df_draft.columns if col not in numericos]

# 2. Fazer o groupby
df_draft_agg = (
    df_draft
    .groupby(chaves, as_index=False)[numericos]
    .max()
)

df_draft_agg['PDV'].value_counts()

PDV
20998    1209
23711    1190
20997    1182
20993    1172
20996    1161
         ... 
24269     490
24253     472
24268     452
24254     439
24258     336
Name: count, Length: 75, dtype: int64

In [32]:
df_draft[df_draft['SKU']==1634]

Empty DataFrame
Columns: [PDV, SKU, curva, categoria, proj_mar, proj_mar+1, ESTOQUE ATUAL, ESTOQUE EM TRANSITO, PEDIDO PENDENTE, DDV PREVISTO, preço, SKU_FINAL, C202412, C202413, C202414, C202415, C202416, C202417, C202501, C202502, C202503, C202504, C202505, C202506, C202507, C202508, C202509, C202510, C202511, C202512]
Index: []

[0 rows x 30 columns]

In [33]:
df_draft1 = df_draft_agg

In [34]:
df_draft1.columns

Index(['PDV', 'SKU', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', 'C202412', 'C202413', 'C202414',
       'C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511', 'C202512'],
      dtype='object')

In [35]:
df_draft1.to_clipboard()

In [36]:
df_final['PDV'] = df_final['PDV'].astype('str')
df_final['Código'] = df_final['Código'].astype('str')


df_final = pd.merge(left=df_final,right=df_draft1,left_on=['PDV','Código'],right_on=['PDV','SKU'],how='left')
df_final.shape

(34265, 60)

In [37]:
df_final[df_final['Código']=='1634'].head()

Ciclo Região Canal Código                           Descrição  IAF  \
12936  202515    NNE  Loja   1634  NSPA GEL ESF CPO MORANGO RUBY 175G  Não   
12937  202515    NNE  Loja   1634  NSPA GEL ESF CPO MORANGO RUBY 175G  Não   
12938  202515    NNE  Loja   1634  NSPA GEL ESF CPO MORANGO RUBY 175G  Não   
12939  202515    NNE  Loja   1634  NSPA GEL ESF CPO MORANGO RUBY 175G  Não   
12940  202515    NNE  Loja   1634  NSPA GEL ESF CPO MORANGO RUBY 175G  Não   

      Tipo de pedido Foco Unidade de negócio       Marca  ... C202503 C202504  \
12936       Especial  Não                BOT  NATIVA SPA  ...     NaN     NaN   
12937       Especial  Não                BOT  NATIVA SPA  ...     NaN     NaN   
12938       Especial  Não                BOT  NATIVA SPA  ...     NaN     NaN   
12939       Especial  Não                BOT  NATIVA SPA  ...     NaN     NaN   
12940       Especial  Não                BOT  NATIVA SPA  ...     NaN     NaN   

       C202505 C202506 C202507 C202508 C202509 C202510 C202511 C202512  
12936      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN  
12937      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN  
12938      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN  
12939      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN  
12940      NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN  

[5 rows x 60 columns]

In [38]:
df_final['PDV'].value_counts()

PDV
12522    445
12817    445
12818    445
12820    445
12823    445
        ... 
24257    445
24268    445
24269    445
24293    445
23813    445
Name: count, Length: 77, dtype: int64

In [39]:
df_final = df_final.drop(columns=['Sortimento P', 'Sortimento M',
       'Sortimento G','MARCA'])

In [40]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")


In [41]:
calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)
calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]


calendario = calendario[calendario['MARCA'] == "BOTICARIO"]

calendario = calendario.drop(columns='MARCA')

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 2).astype(str).str.zfill(2) # >>>>>>>>> MUDAR PRA CICLO CORRETO 

ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]


# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]


filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)

filtered_calendario


Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO       Date  NUM_CICLO  \
2367  C202514   2025-09-22 2025-10-12       21 2025-09-22         14   

     ANO_CICLO CICLOMAIS2  dias_ate_inicio  
2367     C2025    C202516               25

In [42]:
filtered_calendario['MATCH'] = 1

In [43]:
df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

In [44]:
df_draft['PDV'] = df_draft['PDV'].astype(str)

In [45]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','MATCH','dias_ate_inicio']], on='MATCH',how='left')
df_final.shape

(34265, 61)

In [46]:
df_final['Código'] = df_final['Código'].astype('Int64') 
df_final['PDV'] = df_final['PDV'].astype('Int64') 

In [47]:
df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype('Int64')
df_bi_preco.head()

SKU1   SKU2                            Descrição  UF      PC      PV  \
0  84918  84918  ESTJ BOTI CALENDARIO ADVENTO NAT/24  AL  393.70  1300.0   
1  84918  84918  ESTJ BOTI CALENDARIO ADVENTO NAT/24  BA  436.73  1300.0   
2  84918  84918  ESTJ BOTI CALENDARIO ADVENTO NAT/24  SE  379.94  1300.0   
3  54230  54230         MALBEC DES COL 20 ANOS 100ml  AL  138.54   499.9   
4  54230  54230         MALBEC DES COL 20 ANOS 100ml  BA  148.66   499.9   

  chave sku2 chave sku1  
0    AL84918    AL84918  
1    BA84918    BA84918  
2    SE84918    SE84918  
3    AL54230    AL54230  
4    BA54230    BA54230

In [48]:


df_final = pd.merge(left=df_final,right=df_bi_preco,right_on=['UF','SKU2'],left_on=['UF','Código'],how='left')
df_final.shape   

(34265, 68)

In [49]:
df_bi_preco['SKU1'] = df_bi_preco['SKU1'].fillna(0)

In [50]:
# Conversão segura para Int64 (nullable)
df_bi_preco['SKU1'] = pd.to_numeric(df_bi_preco['SKU1'], errors='coerce').astype('Int64')

# Realiza o merge
df_final = pd.merge(
    left=df_final,
    right=df_bi_preco[['SKU1', 'SKU2', 'UF', 'PC', 'PV']],
    right_on=['UF', 'SKU1'],
    left_on=['UF', 'Código'],
    how='left'
)

# Verifica o resultado
print(df_final.shape)


(34265, 72)


In [51]:
df_final['PRECO DE COMPRA'] = np.where(~df_final['PC_x'].isna(),df_final['PC_x'],df_final['PC_y'])

df_final['PRECO DE VENDA'] = np.where(~df_final['PV_x'].isna(),df_final['PV_x'],df_final['PV_y'])



In [52]:
df_final['CANAL'] = np.where((df_final['CANAL'] == 'LJ') | (df_final['CANAL'] == 'HIB'), "TODOS" , np.where((df_final['CANAL'] == 'CD') | (df_final['CANAL'] == 'VD'), "VD", df_final['CANAL']))

df_final['CANAL'].value_counts()

CANAL
TODOS    27145
VD        7120
Name: count, dtype: int64

In [53]:
df_final = df_final.drop_duplicates()

In [54]:
df_final = df_final.drop(columns=['SKU1_x','SKU1_y','SKU2_x','SKU2_y','PC_x', 'PV_x','PC_y', 'PV_y','Subcategoria',
'Quantidade por caixa'
])

In [55]:
df_final['UFPRODUTO'] = df_final['UF'].astype(str) + df_final['Código'].astype(str)


In [56]:
df_final = df_final.rename(columns={'Compra inteligente Próximo Ciclo + 1':'Compra inteligente Próximo Ciclo','Arquivo_Origem': 'MARCA'})

In [57]:
df_final = df_final[~df_final['Marca'].isna()]
df_final['Marca'].isna().sum()

np.int64(0)

In [58]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SKU', 'curva',
       'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', 'C202412', 'C202413', 'C202414', 'C202415', 'C202416',
       'C202417', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C202511',
       'C202512', 'Ciclo_y', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO',
       'dias_ate_inicio', 'Descrição_y', 'chave sku2', 'chave sku1',
       'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO'],
      dtype='object

In [59]:
df_vdc = pd.read_csv(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C10\VENDA VITORIA 2024\VENDA VITORIA.csv")

df_vdc['PRODUTO'] = df_vdc['PRODUTO'].astype('Int64')

df_final['Código'] = df_final['Código'].astype('Int64')

df_final =pd.merge(left=df_final,right=df_vdc,left_on= ['PDV','Código'],right_on= ['PDV GINSENG','PRODUTO'],how='left' )

df_final[df_final.columns[-1]] = df_final[df_final.columns[-1]].fillna(0)

In [60]:
df_vdc[df_vdc['PRODUTO']== 74043].head()

PDV GINSENG  PRODUTO  202401  202402  202403  202404  202405  202406  \
1235        23701    74043      12      24      12      16       8      14   
3033        23702    74043       2      22       8      22      10      14   
5171        23703    74043      10      18       6      18       6       2   

      202407  202408  202409  202410  202411  202412  202413  202414  202415  \
1235       6      14      12       0       8      10       4      42       0   
3033      14      10      12       8      22       6      14      36      10   
5171      20       0      10       2      22       4       2      26       2   

      202416  
1235      14  
3033       0  
5171      16

In [61]:
df_final = df_final.fillna(0)


In [62]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SKU', 'curva',
       'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', 'C202412', 'C202413', 'C202414', 'C202415', 'C202416',
       'C202417', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C202511',
       'C202512', 'Ciclo_y', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO',
       'dias_ate_inicio', 'Descrição_y', 'chave sku2', 'chave sku1',
       'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG',
     

In [63]:
df_final.columns[-16:]

Index(['202401', '202402', '202403', '202404', '202405', '202406', '202407',
       '202408', '202409', '202410', '202411', '202412', '202413', '202414',
       '202415', '202416'],
      dtype='object')

In [64]:
df_final.to_clipboard()

In [65]:
import re

# identificar colunas de ciclo puro (ex: '202407')
colunas_ciclo_puro = [col for col in df_final.columns[-16:]]

for col in colunas_ciclo_puro:
    col_hist = f'C{col}'
    if col_hist in df_final.columns:
        # mantém o maior valor entre a coluna histórica e a pura
        df_final[col_hist] = df_final[[col_hist, col]].max(axis=1)

# remove as colunas puras
if colunas_ciclo_puro:
    df_final.drop(columns=colunas_ciclo_puro, inplace=True)


In [66]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SKU', 'curva',
       'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', 'C202412', 'C202413', 'C202414', 'C202415', 'C202416',
       'C202417', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C202511',
       'C202512', 'Ciclo_y', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO',
       'dias_ate_inicio', 'Descrição_y', 'chave sku2', 'chave sku1',
       'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG',
     

In [67]:
df_irece = pd.read_csv(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\DADOS DOURADO\VENDA\COMPILADO_VENDAS.csv", sep=';')

df_irece['DATA_VENDA'] = pd.to_datetime(df_irece['DATA_VENDA'], dayfirst=True)

df_irece = pd.merge(df_irece,calendario[['Ciclo','Date']],how='left', left_on='DATA_VENDA',right_on='Date')

df_irece.head()

DATA_VENDA    PDV  pdvs cp                                       DESC PDV  \
0 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   
1 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   
2 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   
3 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   
4 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   

   Código                                 Descrição  Quantidade Faturamento  \
0    1004             FLORATTA DES COL MY BLUE 75ml           1       98,99   
1    4539      BOTIK CR FAC FIRMADOR AC/HIAL 40g V2           1      129,05   
2   29046  BOTICOLL CONNEX DES BDY SPR 100ml V6 PCK           1        38,9   
3   47154                 CBEM DES ROLL S/ALUM 55ml           1       21,98   
4   47411                          ARBO NECESS LONA           1       57,26   

     Ciclo       Date  
0  C202505 2025-04-01  
1  C202505 2025-04-01  
2  C202505 2025-04-01  
3  C202505 2025-04-01  
4  C202505 2025-04-01

In [68]:
df_irece_agrupado = df_irece.groupby(['PDV','Código','Ciclo'])['Quantidade'].sum().reset_index()

df_pivotado = df_irece_agrupado.pivot(index=['PDV', 'Código'], columns='Ciclo', values='Quantidade').reset_index()

df_pivotado = df_pivotado.fillna(0)

In [69]:
df_final.columns[37:55]

Index(['C202413', 'C202414', 'C202415', 'C202416', 'C202417', 'C202501',
       'C202502', 'C202503', 'C202504', 'C202505', 'C202506', 'C202507',
       'C202508', 'C202509', 'C202510', 'C202511', 'C202512', 'Ciclo_y'],
      dtype='object')

In [70]:
for col_c in df_final.columns[37:55]:
    sufixo = col_c[1:]  # Remove o 'C' do início, ex: 'C202407' -> '202407'
    df_final.columns = df_final.columns.str.replace("C20", "20", regex=True)


df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SKU', 'curva',
       'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', '202412', '202413', '202414', '202415', '202416', '202417',
       '202501', '202502', '202503', '202504', '202505', '202506', '202507',
       '202508', '202509', '202510', '202511', '202512', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'Descrição_y', 'chave sku2', 'chave sku1', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG', 'PRODUTO'],
      dtype

In [71]:
df_final = pd.merge(df_final,df_pivotado,how='left',on=['PDV','Código'])

df_final = df_final.fillna(0)

df_final.head()

Ciclo_x Região Canal  Código                Descrição_x  IAF  \
0   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   
1   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   
2   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   
3   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   
4   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   

  Tipo de pedido Foco Unidade de negócio Marca  ... C202415 C202416 C202417  \
0        Semanal  Não                BOT  ARBO  ...     0.0     0.0     0.0   
1        Semanal  Não                BOT  ARBO  ...     0.0     0.0     0.0   
2        Semanal  Não                BOT  ARBO  ...     0.0     0.0     0.0   
3        Semanal  Não                BOT  ARBO  ...     0.0     0.0     0.0   
4        Semanal  Não                BOT  ARBO  ...     0.0     0.0     0.0   

  C202501 C202502 C202503 C202504 C202505  C202506  C202507  
0     0.0     0.0     0.0     0.0     0.0      0.0      0.0  
1     0.0     0.0     0.0     0.0     0.0      0.0      0.0  
2     0.0     0.0     0.0     0.0     0.0      0.0      0.0  
3     0.0     0.0     0.0     0.0     0.0      0.0      0.0  
4     0.0     0.0     0.0     0.0     0.0      0.0      0.0  

[5 rows x 91 columns]

In [72]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SKU', 'curva',
       'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', '202412', '202413', '202414', '202415', '202416', '202417',
       '202501', '202502', '202503', '202504', '202505', '202506', '202507',
       '202508', '202509', '202510', '202511', '202512', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'Descrição_y', 'chave sku2', 'chave sku1', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG', 'PRODUTO', 'C202401',
 

In [73]:


# 1. Identificar colunas no formato 'C2024xx', 'C2025xx', etc.
colunas_ciclo_c = [col for col in df_pivotado.columns if re.fullmatch(r'C20\d{4}', col)]

for col_c in colunas_ciclo_c:
    sufixo = col_c[1:]  # Remove o 'C' do início, ex: 'C202407' -> '202407'
    col_hist = col_c
    
    if col_hist in df_final.columns:
        # Pega o maior valor entre a coluna de histórico e a de ciclo com "C"
        df_final[col_hist] = df_final[[col_hist, col_c]].max(axis=1)

# (Opcional) Remover as colunas 'C20xxxx' após o merge
df_final.drop(columns=colunas_ciclo_c, inplace=True)


In [74]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SKU', 'curva',
       'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', '202412', '202413', '202414', '202415', '202416', '202417',
       '202501', '202502', '202503', '202504', '202505', '202506', '202507',
       '202508', '202509', '202510', '202511', '202512', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'Descrição_y', 'chave sku2', 'chave sku1', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG', 'PRODUTO'],
      dtype

In [75]:
colunas_ciclo_c = [col for col in df_pivotado.columns if re.fullmatch(r'C20\d{4}', col)]

for col_c in colunas_ciclo_c:
    sufixo = col_c[1:]  # Remove o 'C' do início, ex: 'C202407' -> '202407'
    col_hist = col_c
    print(sufixo,col_c)


202401 C202401
202402 C202402
202403 C202403
202404 C202404
202405 C202405
202406 C202406
202407 C202407
202408 C202408
202409 C202409
202410 C202410
202411 C202411
202412 C202412
202413 C202413
202414 C202414
202415 C202415
202416 C202416
202417 C202417
202501 C202501
202502 C202502
202503 C202503
202504 C202504
202505 C202505
202506 C202506
202507 C202507


In [76]:
df_final = df_final.drop(columns=['Ciclo_y'])

In [77]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SKU', 'curva',
       'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', '202412', '202413', '202414', '202415', '202416', '202417',
       '202501', '202502', '202503', '202504', '202505', '202506', '202507',
       '202508', '202509', '202510', '202511', '202512', 'INICIO CICLO',
       'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'Descrição_y', 'chave sku2',
       'chave sku1', 'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO',
       'PDV GINSENG', 'PRODUTO'],
      dtype='object')

In [78]:
df_final = df_final.drop_duplicates()
df_final.shape

(34265, 66)

In [79]:
df_final['chave'] = df_final['PDV'].astype('str') + df_final['Código'].astype('str')

In [80]:
df_final = df_final.fillna(0)


In [81]:
df_final.columns[36:54]

Index(['202412', '202413', '202414', '202415', '202416', '202417', '202501',
       '202502', '202503', '202504', '202505', '202506', '202507', '202508',
       '202509', '202510', '202511', '202512'],
      dtype='object')

In [82]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SKU', 'curva',
       'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', '202412', '202413', '202414', '202415', '202416', '202417',
       '202501', '202502', '202503', '202504', '202505', '202506', '202507',
       '202508', '202509', '202510', '202511', '202512', 'INICIO CICLO',
       'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'Descrição_y', 'chave sku2',
       'chave sku1', 'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO',
       'PDV GINSENG', 'PRODUTO', 'chave'],
      dtype='

In [83]:
# Define list of target columns
sales_2024_cols = df_final.columns[36:54]
# Create a new column with the row-wise max
df_final['PICO DE VENDAS 2024'] = df_final[sales_2024_cols].max(axis=1)



In [84]:
vendas_6_meses = df_final.columns[48:54]

df_final['Pico Vendas Ultimos 6 ciclos'] = df_final[vendas_6_meses].max(axis=1)

In [85]:
df_final.columns[37:44]

Index(['202413', '202414', '202415', '202416', '202417', '202501', '202502'], dtype='object')

In [86]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SKU', 'curva',
       'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', '202412', '202413', '202414', '202415', '202416', '202417',
       '202501', '202502', '202503', '202504', '202505', '202506', '202507',
       '202508', '202509', '202510', '202511', '202512', 'INICIO CICLO',
       'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'Descrição_y', 'chave sku2',
       'chave sku1', 'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO',
       'PDV GINSENG', 'PRODUTO', 'chave', 'PICO DE VENDA

In [87]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SKU', 'curva',
       'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', '202412', '202413', '202414', '202415', '202416', '202417',
       '202501', '202502', '202503', '202504', '202505', '202506', '202507',
       '202508', '202509', '202510', '202511', '202512', 'INICIO CICLO',
       'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'Descrição_y', 'chave sku2',
       'chave sku1', 'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO',
       'PDV GINSENG', 'PRODUTO', 'chave', 'PICO DE VENDA

In [88]:
df_final.columns[36:54]

Index(['202412', '202413', '202414', '202415', '202416', '202417', '202501',
       '202502', '202503', '202504', '202505', '202506', '202507', '202508',
       '202509', '202510', '202511', '202512'],
      dtype='object')

In [89]:
df_final.head()

Ciclo_x Região Canal  Código                Descrição_x  IAF  \
0   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   
1   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   
2   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   
3   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   
4   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   

  Tipo de pedido Foco Unidade de negócio Marca  ... chave sku2 chave sku1  \
0        Semanal  Não                BOT  ARBO  ...    AL50052    AL50052   
1        Semanal  Não                BOT  ARBO  ...    AL50052    AL50052   
2        Semanal  Não                BOT  ARBO  ...    AL50052    AL50052   
3        Semanal  Não                BOT  ARBO  ...    AL50052    AL50052   
4        Semanal  Não                BOT  ARBO  ...    AL50052    AL50052   

  PRECO DE COMPRA PRECO DE VENDA UFPRODUTO PDV GINSENG PRODUTO       chave  \
0           11.72           37.9   AL50052         0.0       0  1252250052   
1           11.72           37.9   AL50052         0.0       0  1281750052   
2           11.72           37.9   AL50052         0.0       0  1281850052   
3           11.72           37.9   AL50052         0.0       0  1282050052   
4           11.72           37.9   AL50052         0.0       0  1282350052   

   PICO DE VENDAS 2024  Pico Vendas Ultimos 6 ciclos  
0                  2.0                           0.0  
1                  5.0                           0.0  
2                  1.0                           1.0  
3                  1.0                           0.0  
4                  1.0                           0.0  

[5 rows x 69 columns]

In [90]:
# Define as colunas mensais
colunas_mensais = df_final.columns[36:54]

# Função de cálculo por grupo
def calcular_crescimento(grupo):
    soma_mensal = grupo[colunas_mensais].sum()
    variacao_mensal = soma_mensal.pct_change().dropna()
    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

    if len(variacao_mensal) == 0:
        return pd.Series({'CRESCIMENTO': np.nan})

    media = variacao_mensal.mean()
    desvio = variacao_mensal.std()

    limite_sup = media + 2 * desvio
    limite_inf = media - 2 * desvio

    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]
    crescimento = round(variacoes_filtradas.mean(), 4)
    return pd.Series({'CRESCIMENTO': crescimento})

# Aplica a função por PDV
crescimento_por_pdv = (
    df_final
    .groupby('PDV')
    .apply(calcular_crescimento)   # retorna índice com PDV
    .reset_index(level=0)          # reseta só o nível PDV
)

# Merge do resultado de volta no dataframe original
df_final = df_final.merge(crescimento_por_pdv, on='PDV', how='left')


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_2580\3082173574.py:27: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  .apply(calcular_crescimento)   # retorna índice com PDV


In [91]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[36:54]

# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

df_final['CRESCIMENTO_GERAL'] = 0.2

CRESCIMENTO


np.float64(0.0857)

In [92]:
df_final.columns[36:54]

Index(['202412', '202413', '202414', '202415', '202416', '202417', '202501',
       '202502', '202503', '202504', '202505', '202506', '202507', '202508',
       '202509', '202510', '202511', '202512'],
      dtype='object')

In [93]:
vendas_todos_historicos = df_final.columns[36:54]

df_final['MEDIANA DO HISTÓRICO'] = df_final[vendas_todos_historicos].median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[vendas_todos_historicos].mean(axis=1)

medi = df_final.groupby(['CANAL','UF','Código'])['MEDIANA DO HISTÓRICO'].max().reset_index()
medi = medi.rename(columns={'MEDIANA DO HISTÓRICO':'med_por_canal'})

df_final = pd.merge(left=df_final, right=medi,on=['CANAL','UF','Código'],how='left')

medi

CANAL   UF  Código  med_por_canal
0     TODOS   AL    1428            0.0
1     TODOS   AL    1634            0.0
2     TODOS   AL    1640            0.0
3     TODOS   AL    1650            0.0
4     TODOS   AL    1806            0.0
...     ...  ...     ...            ...
4445     VD  VDC   88471            0.0
4446     VD  VDC   88563            0.0
4447     VD  VDC   88730            0.0
4448     VD  VDC   89421            0.0
4449     VD  VDC   89495            0.0

[4450 rows x 4 columns]

In [94]:
df_final.columns[39]

'202415'

In [95]:
mesmo_ciclo_ano_passado = df_final.columns[39]
ciclo_ano_passado = df_final.columns[39]
df_final[ciclo_ano_passado] = df_final[mesmo_ciclo_ano_passado]

In [96]:
'''df_final['CRESCIMENTO_GERAL'] = 0.2
df_final['CRESCIMENTO'] = 0.2'''

"df_final['CRESCIMENTO_GERAL'] = 0.2\ndf_final['CRESCIMENTO'] = 0.2"

In [97]:
df_final['CRESCIMENTO_FINAL'] = df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'] #crescimento do pdv

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']>0.8,0.8,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']<0,0,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

df_final['MEDIANA DO HISTÓRICO2'] = np.where(df_final['MEDIANA DO HISTÓRICO']==0,df_final['MEDIA DO HISTÓRICO'] ,df_final['MEDIANA DO HISTÓRICO'])

# Primeiro cálculo intermediário
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO_FINAL'] * df_final[ciclo_ano_passado] + df_final[ciclo_ano_passado] <1,
                                    round(df_final['CRESCIMENTO_FINAL'] * df_final['MEDIANA DO HISTÓRICO2']+ df_final['MEDIANA DO HISTÓRICO2'],0), 
                                    round(df_final['CRESCIMENTO_FINAL']*df_final[ciclo_ano_passado]+df_final[ciclo_ano_passado],0))


df_final.shape

(34265, 77)

In [98]:
df_final['PDV'].value_counts()

PDV
12522    445
12817    445
12818    445
12820    445
12823    445
        ... 
24257    445
24268    445
24269    445
24293    445
23813    445
Name: count, Length: 77, dtype: Int64

In [99]:
df_final.head()

Ciclo_x Região Canal  Código                Descrição_x  IAF  \
0   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   
1   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   
2   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   
3   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   
4   202515    NNE  Loja   50052  ARBO LOC DES HID CPO 75ml  Não   

  Tipo de pedido Foco Unidade de negócio Marca  ... PICO DE VENDAS 2024  \
0        Semanal  Não                BOT  ARBO  ...                 2.0   
1        Semanal  Não                BOT  ARBO  ...                 5.0   
2        Semanal  Não                BOT  ARBO  ...                 1.0   
3        Semanal  Não                BOT  ARBO  ...                 1.0   
4        Semanal  Não                BOT  ARBO  ...                 1.0   

  Pico Vendas Ultimos 6 ciclos CRESCIMENTO CRESCIMENTO_GERAL  \
0                          0.0      0.0762               0.2   
1                          0.0      0.0867               0.2   
2                          1.0      0.1065               0.2   
3                          0.0      0.0882               0.2   
4                          0.0      0.0745               0.2   

  MEDIANA DO HISTÓRICO MEDIA DO HISTÓRICO med_por_canal CRESCIMENTO_FINAL  \
0                  0.0           0.111111           0.0            0.2762   
1                  0.0           0.555556           0.0            0.2867   
2                  0.0           0.055556           0.0            0.3065   
3                  0.0           0.055556           0.0            0.2882   
4                  0.0           0.111111           0.0            0.2745   

   MEDIANA DO HISTÓRICO2  PV GINSENG  
0               0.111111         0.0  
1               0.555556         1.0  
2               0.055556         0.0  
3               0.055556         0.0  
4               0.111111         0.0  

[5 rows x 77 columns]

In [100]:
df_final = df_final.drop(columns=['MEDIANA DO HISTÓRICO2'] )

In [101]:
df_final.columns[38:45]

Index(['202414', '202415', '202416', '202417', '202501', '202502', '202503'], dtype='object')

In [102]:
df_final.columns[49:54]

Index(['202508', '202509', '202510', '202511', '202512'], dtype='object')

In [103]:
df_final = df_final.rename(columns={df_final.columns[49]: "C-4", df_final.columns[50]: "C-3",df_final.columns[51]: "C-2",df_final.columns[52]: "C-1",df_final.columns[53]: "Atual"})

In [104]:
df_final.columns[40:49]

Index(['202416', '202417', '202501', '202502', '202503', '202504', '202505',
       '202506', '202507'],
      dtype='object')

In [105]:
df_final.drop(columns=df_final.columns[40:49], inplace=True)
df_final.drop(columns=df_final.columns[37:39], inplace=True)

In [106]:
df_final['COBERTURA ATUAL'] = df_final['ESTOQUE ATUAL'].astype(float) / df_final['DDV PREVISTO'].astype(float)

In [107]:
df_final['COBERTURA ATUAL'] = df_final['COBERTURA ATUAL'].replace([np.inf, -np.inf], 0)

df_final['COBERTURA ATUAL'] = round(df_final['COBERTURA ATUAL'],0)

In [108]:
df_final['COBERTURA ATUAL'].value_counts()

COBERTURA ATUAL
0.0       6787
100.0      699
50.0       447
40.0       375
20.0       342
          ... 
245.0        1
778.0        1
811.0        1
1967.0       1
644.0        1
Name: count, Length: 641, dtype: int64

In [109]:
df_final["DDV PREVISTO"] = df_final["DDV PREVISTO"].astype(float)

df_final["DDV PREVISTO"] = df_final["DDV PREVISTO"].fillna(0)

In [110]:
df_final['PDV'].value_counts()

PDV
12522    445
12817    445
12818    445
12820    445
12823    445
        ... 
24257    445
24268    445
24269    445
24293    445
23813    445
Name: count, Length: 77, dtype: Int64

In [111]:
r'''colunas_chave = [c for c in df_final.columns if c not in ["DDV PREVISTO", "COBERTURA ATUAL"]]


# encontrar índice da linha com maior DDV e depois maior COBERTURA
idx = (
df_final
.sort_values(["DDV PREVISTO", "COBERTURA ATUAL"], ascending=[False, False])
.groupby(colunas_chave, as_index=False)
.head(1)
)


# reordenar colunas como no original
df_final_dedup = idx[df_final.columns.tolist()].reset_index(drop=True)'''

df_final_dedup = df_final

In [112]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SKU', 'curva',
       'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', '202412', '202415', 'C-4', 'C-3', 'C-2', 'C-1', 'Atual',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'Descrição_y', 'chave sku2', 'chave sku1', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG', 'PRODUTO', 'chave',
       'PICO DE VENDAS 2024', 'Pico Vendas Ultimos 6 ciclos', 'CRESCIMENTO',
       'CRESCIMENTO_GERAL', 'MEDIANA DO HISTÓRICO', 'MEDIA DO HISTÓRICO',


In [113]:
# Columns to bring up front
priority_cols = [
    'SKU',	'Marca',	'INICIO CICLO',
    'FIM CICLO',	'DURAÇÃO',	'PRECO DE COMPRA',	'PRECO DE VENDA',
    'UFPRODUTO',	'Item Desativado',	'Data Prevista Regularização',
    'ANALISTA',	'UF',	'CANAL',	'PDV',	'DESCRIÇÃO PDV',	'Classe',
    'Descrição',	'Categoria',
	'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',	'COBERTURA ATUAL',
    'Pedido Pendente',	'PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos',
    'C-4',	'C-3',	'C-2',	'C-1',	'Histórico de Vendas do Ciclo Atual',
    'Dias sem venda'
]

# All remaining columns
other_cols = [col for col in df_final_dedup.columns if col not in priority_cols]

# Reorder
'Ação consumidor', 'Percentual de desconto consumidor', 'Ação revendedor', 'Percentual de desconto revendedor', '202408'


('Ação consumidor',
 'Percentual de desconto consumidor',
 'Ação revendedor',
 'Percentual de desconto revendedor',
 '202408')

In [114]:
df_final_dedup[df_final_dedup['PDV'] == 21007]

Ciclo_x Região  Canal  Código                        Descrição_x  IAF  \
39      202515    NNE   Loja   50052          ARBO LOC DES HID CPO 75ml  Não   
116     202515    NNE  Todos   57640                ARBO NECESSAIRE PES  Não   
193     202515    NNE  Todos   51803            BOTI BABY COND V2 400ml  Não   
270     202515    NNE  Todos   52023        BOTI BABY LOC HID CPO 400ml  Não   
347     202515    NNE  Todos   52025    BOTI BABY SAB LIQ GLIC V2 400ml  Não   
...        ...    ...    ...     ...                                ...  ...   
33919   202515    NNE     VD   36826  REF MAKE B PO COMP FAC HYAL 70 8g  Não   
33996   202515    NNE     VD   46568                 SOPHIE BOLSA NYLON  Não   
34073   202515    NNE     VD   47949             THE BLEND EDP 100ml V2  Não   
34150   202515    NNE     VD   49038         ZAAD BALM POS BARB 110g V4  Não   
34227   202515    NNE     VD   48368        ZAAD ESPUM P/ BARB 200ml V4  Não   

      Tipo de pedido Foco Unidade de negócio      Marca  ...  \
39           Semanal  Não                BOT       ARBO  ...   
116          Semanal  Não                BOT       ARBO  ...   
193          Semanal  Não                BOT  BOTI BABY  ...   
270          Semanal  Não                BOT  BOTI BABY  ...   
347          Semanal  Não                BOT  BOTI BABY  ...   
...              ...  ...                ...        ...  ...   
33919        Semanal  Não                BOT    MAKE B.  ...   
33996        Semanal  Não                BOT     SOPHIE  ...   
34073        Semanal  Não                BOT  THE BLEND  ...   
34150        Semanal  Não                BOT       ZAAD  ...   
34227        Semanal  Não                BOT       ZAAD  ...   

      PICO DE VENDAS 2024 Pico Vendas Ultimos 6 ciclos CRESCIMENTO  \
39                    0.0                          0.0         NaN   
116                   0.0                          0.0         NaN   
193                   0.0                          0.0         NaN   
270                   0.0                          0.0         NaN   
347                   0.0                          0.0         NaN   
...                   ...                          ...         ...   
33919                 0.0                          0.0         NaN   
33996                 0.0                          0.0         NaN   
34073                 0.0                          0.0         NaN   
34150                 0.0                          0.0         NaN   
34227                 0.0                          0.0         NaN   

      CRESCIMENTO_GERAL MEDIANA DO HISTÓRICO MEDIA DO HISTÓRICO med_por_canal  \
39                  0.2                  0.0                0.0           0.0   
116                 0.2                  0.0                0.0           0.0   
193                 0.2                  0.0                0.0           3.0   
270                 0.2                  0.0                0.0           3.0   
347                 0.2                  0.0                0.0           8.0   
...                 ...                  ...                ...           ...   
33919               0.2                  0.0                0.0           0.0   
33996               0.2                  0.0                0.0           1.0   
34073               0.2                  0.0                0.0          17.0   
34150               0.2                  0.0                0.0           0.0   
34227               0.2                  0.0                0.0           1.0   

      CRESCIMENTO_FINAL  PV GINSENG  COBERTURA ATUAL  
39                  NaN         NaN              NaN  
116                 NaN         NaN              NaN  
193                 NaN         NaN              NaN  
270                 NaN         NaN              NaN  
347                 NaN         NaN              NaN  
...                 ...         ...              ...  
33919               NaN         NaN              NaN  
33996               NaN

In [115]:
df_final_dedup.drop(columns=['dias_ate_inicio','SKU_FINAL',
                             'CRESCIMENTO'],inplace=True)

In [116]:
df_final_dedup['INICIO CICLO'] = pd.to_datetime(df_final_dedup['INICIO CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_final_dedup['FIM CICLO'] = pd.to_datetime(df_final_dedup['FIM CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

In [117]:
df_final_dedup['Percentual de desconto revendedor'] = np.where((df_final_dedup['Percentual de desconto revendedor'].isna()) & (~df_final_dedup['Percentual de desconto consumidor'].isna()),df_final_dedup['Percentual de desconto consumidor'],df_final_dedup['Percentual de desconto revendedor'])

In [118]:
df_pdv_origi['PDV'] = df_pdv_origi['PDV'].astype('Int64')
df_final_dedup['PDV'] = df_final_dedup['PDV'].astype('Int64')


df_final_dedup = pd.merge(left=df_final_dedup,right=df_pdv_origi[['PDV','CANAL','UF']],how='left',on='PDV')

In [119]:
df_final_dedup['Código'].isna().sum()

np.int64(0)

In [120]:
df_irece_agrupado = df_irece.groupby(['PDV','Código','Ciclo'])['Quantidade'].sum().reset_index()

In [121]:
df_final_dedup = df_final_dedup.rename(columns={'CANAL_x':'CANAL','UF_X':'UF','Marca':'LINHA'})


In [122]:
df_final_dedup['PDV'].value_counts()

PDV
12522    445
12817    445
12818    445
12820    445
12823    445
        ... 
24257    445
24268    445
24269    445
24293    445
23813    445
Name: count, Length: 77, dtype: Int64

In [123]:
df_final_dedup = df_final_dedup.rename(columns={'UF_x':'UF','DESCRICAO_y':'DESCRICAO'})

In [124]:
df_final_dedup = df_final_dedup.drop(columns={'CANAL_y', 'UF_y'})


In [125]:
df_final_dedup['Estoque Total'] = df_final_dedup['ESTOQUE ATUAL'].astype(float) + df_final_dedup['ESTOQUE EM TRANSITO'].astype(float) + df_final_dedup['PEDIDO PENDENTE'].astype(float)

In [126]:
ciclo_ano_passado

'202415'

In [127]:
df_final_dedup.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição_x', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'LINHA', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'SKU', 'curva',
       'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       '202412', '202415', 'C-4', 'C-3', 'C-2', 'C-1', 'Atual', 'INICIO CICLO',
       'FIM CICLO', 'DURAÇÃO', 'Descrição_y', 'chave sku2', 'chave sku1',
       'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG',
       'PRODUTO', 'chave', 'PICO DE VENDAS 2024',
       'Pico Vendas Ultimos 6 ciclos', 'CRESCIMENTO_GERAL',
       'MEDIANA DO HISTÓRICO', 'MEDIA DO HISTÓRICO', 'med_por_canal',
       'CRESCIMENTO_FINAL', 'P

In [128]:
df_final_dedup = df_final_dedup.drop(columns='Descrição_y')

df_final_dedup = df_final_dedup.rename(columns={'Descrição_x':'Descrição'})

In [129]:
df_final_dedup = df_final_dedup[['DURAÇÃO','CANAL','ANALISTA','SUPERVISOR','UF','chave','PDV','DESCRIÇÃO PDV','Código','Descrição','LINHA','Categoria','curva','Percentual de desconto consumidor','Ação consumidor',
                                 'Percentual de desconto revendedor','Ação revendedor','C-4', 'C-3', 'C-2', 'C-1','Atual',ciclo_ano_passado ,'ESTOQUE ATUAL','ESTOQUE EM TRANSITO','PEDIDO PENDENTE','Estoque Total',
                                 'DDV PREVISTO','COBERTURA ATUAL','proj_mar', 'proj_mar+1','MEDIA DO HISTÓRICO','PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos','PRECO DE COMPRA',
                                'PRECO DE VENDA','PV GINSENG']]

In [130]:
df_final_dedup['Percentual de desconto revendedor'] = np.where(df_final_dedup['Percentual de desconto revendedor'] == '0,00', df_final_dedup['Percentual de desconto consumidor'],df_final_dedup['Percentual de desconto revendedor'])

In [131]:
ciclo_ano_passado

'202415'

In [132]:
df_final_dedup = df_final_dedup.drop_duplicates()

In [133]:
df_final_dedup['Valor Sugestão'] = ""

df_final_dedup['Sugestão Abastecimento'] = ""

In [134]:
df_final_dedup[['DDV PREVISTO',
       'COBERTURA ATUAL',]].dtypes

DDV PREVISTO       float64
COBERTURA ATUAL    float64
dtype: object

In [135]:
df_final_dedup[ 'DDV PREVISTO'] =  df_final_dedup['DDV PREVISTO'].fillna(0)

df_final_dedup = df_final_dedup.drop_duplicates()

In [136]:
df_final_dedup[df_final_dedup['chave'] == '2371184387'].head()

DURAÇÃO CANAL   ANALISTA           SUPERVISOR   UF       chave    PDV  \
32171       21    VD  JEFFERSON  Juliana Vasconcelos  VDC  2371184387  23711   

                 DESCRIÇÃO PDV  Código                Descrição  ... proj_mar  \
32171  ER VITORIA DA CONQUISTA   84387  MALBEC DES COL V6 100ml  ...   1505.0   

      proj_mar+1 MEDIA DO HISTÓRICO PICO DE VENDAS 2024  \
32171      242.0         612.388889              2734.0   

      Pico Vendas Ultimos 6 ciclos PRECO DE COMPRA PRECO DE VENDA  PV GINSENG  \
32171                        857.0             0.0            0.0        12.0   

       Valor Sugestão  Sugestão Abastecimento  
32171                                          

[1 rows x 39 columns]

In [137]:
df_final_dedup[df_final_dedup['chave'] == '2371184387']['DDV PREVISTO'].head()


32171    88.7
Name: DDV PREVISTO, dtype: float64

In [138]:
df_final_dedup.head()

DURAÇÃO  CANAL   ANALISTA          SUPERVISOR  UF       chave    PDV  \
0       21  TODOS       LUAN  Efigênia Herculano  AL  1252250052  12522   
1       21  TODOS  JEFFERSON      Maxwell Vieira  AL  1281750052  12817   
2       21  TODOS      PEDRO      Maxwell Vieira  AL  1281850052  12818   
3       21  TODOS   THAYLLAN      Maxwell Vieira  AL  1282050052  12820   
4       21  TODOS   MARCYARA  Efigênia Herculano  AL  1282350052  12823   

     DESCRIÇÃO PDV  Código                  Descrição  ... proj_mar  \
0  MACEIO SHOP EXP   50052  ARBO LOC DES HID CPO 75ml  ...      1.0   
1   SHOPPING PATIO   50052  ARBO LOC DES HID CPO 75ml  ...      1.0   
2      GB SERRARIA   50052  ARBO LOC DES HID CPO 75ml  ...      0.0   
3         ATACADÃO   50052  ARBO LOC DES HID CPO 75ml  ...      0.0   
4      PONTA VERDE   50052  ARBO LOC DES HID CPO 75ml  ...      0.0   

  proj_mar+1 MEDIA DO HISTÓRICO PICO DE VENDAS 2024  \
0        0.0           0.111111                 2.0   
1        0.0           0.555556                 5.0   
2        0.0           0.055556                 1.0   
3        0.0           0.055556                 1.0   
4        0.0           0.111111                 1.0   

  Pico Vendas Ultimos 6 ciclos PRECO DE COMPRA PRECO DE VENDA  PV GINSENG  \
0                          0.0           11.72           37.9         0.0   
1                          0.0           11.72           37.9         1.0   
2                          1.0           11.72           37.9         0.0   
3                          0.0           11.72           37.9         0.0   
4                          0.0           11.72           37.9         0.0   

   Valor Sugestão  Sugestão Abastecimento  
0                                          
1                                          
2                                          
3                                          
4                                          

[5 rows x 39 columns]

In [139]:
df_pdv_origi['PDV'] = df_pdv_origi['PDV'].astype('Int64')



df_pdv_origi = df_pdv_origi.rename(columns={'CANAL':'CANAL_CERTO'})

df_final_dedup= pd.merge(df_final_dedup,df_pdv_origi[['PDV','CANAL_CERTO']],on='PDV',how='inner')

df_final_dedup['CANAL']= df_final_dedup['CANAL_CERTO']


df_final_dedup.columns

Index(['DURAÇÃO', 'CANAL', 'ANALISTA', 'SUPERVISOR', 'UF', 'chave', 'PDV',
       'DESCRIÇÃO PDV', 'Código', 'Descrição', 'LINHA', 'Categoria', 'curva',
       'Percentual de desconto consumidor', 'Ação consumidor',
       'Percentual de desconto revendedor', 'Ação revendedor', 'C-4', 'C-3',
       'C-2', 'C-1', 'Atual', '202415', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Estoque Total', 'DDV PREVISTO', 'COBERTURA ATUAL',
       'proj_mar', 'proj_mar+1', 'MEDIA DO HISTÓRICO', 'PICO DE VENDAS 2024',
       'Pico Vendas Ultimos 6 ciclos', 'PRECO DE COMPRA', 'PRECO DE VENDA',
       'PV GINSENG', 'Valor Sugestão', 'Sugestão Abastecimento',
       'CANAL_CERTO'],
      dtype='object')

In [140]:
# Export to Excel
output_file = f'C:\\Users\\joao.herculano\\Documents\\promoção_BOTI_{ciclo_mais2}.{hoje}.xlsx'
with pd.ExcelWriter(output_file, engine='openpyxl') as writer:
    df_final_dedup.to_excel(writer, index=False)

# Apply styles
wb = load_workbook(output_file)
ws = wb['Sheet1']

# Style header
header_fill = PatternFill(start_color='ADD8E6', end_color='ADD8E6', fill_type='solid')  # Light Blue
header_font = Font(color='FFFFFF', bold=True)  # White & Bold

for cell in ws[1]:
    cell.fill = header_fill
    cell.font = header_font

# Style rows: gray/white alternating
gray_fill = PatternFill(start_color='DDDDDD', end_color='DDDDDD', fill_type='solid')  # Light gray

for i, row in enumerate(ws.iter_rows(min_row=2, max_row=ws.max_row), start=2):
    if i % 2 == 0:
        for cell in row:
            cell.fill = gray_fill

# Save styled workbook
wb.save(output_file)


coisas q saem

Lançamento
Subcategoria
Projeção Próximo Ciclo 
Promoção Próximo Ciclo
Compra inteligente semanal/Sugestão de compra
Compra inteligente Próximo Ciclo
Planograma
Carteira Bloqueada Para Novos Pedidos
Quantidade por caixa
Preço Sell In
Quantidade
Item analisado
Tipo Preço

>>>>>>>>>>>>>NAO ESTÁ PEGANDO O MERGE COM O DF_ESTOQUE


CRIAR PROJEÇÃO DE VENDA DO CICLO ATUAL
Compra inteligente Próximo Ciclo + 1 >>>>>>> RENAME PRA NOROMAL